<a href="https://colab.research.google.com/github/RO-AD/waymo-od-motion-pred/blob/main/tutorial/5_dataset-visualization/hj-dataset-visualization.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

tutorial/5_dataset-visualization/hj-dataset-visualization.ipynb

# 데이터 시각화

- Map 먼저 그리기
  - LaneCenter (차선 중간)
  - RoadLine (차선)
  - RoadEdge (가장자리)
  - StopSign, Crosswalk, SpeedBump, Driveway
- DynamicMapState 그리기
  - TrafficSignalLaneState
- Tracks 그리기


## 환경세팅

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [7]:
VALIDATION_PATH = "/content/drive/MyDrive/waymo-od-dataset/motion_v_1_2_0/uncompressed/scenario/validation/"
filename = VALIDATION_PATH + 'validation.tfrecord-00000-of-00150'

In [3]:
%%capture
!pip3 install --upgrade pip
!pip install waymo-open-dataset-tf-2-11-0==1.5.1 # 최신 버전 라이브러리

In [106]:
import math
import os
import uuid
import time

import numpy as np
import pandas as pd
import tensorflow as tf

from google.protobuf import text_format
from waymo_open_dataset.metrics.ops import py_metrics_ops
from waymo_open_dataset.metrics.python import config_util_py as config_util
from waymo_open_dataset.protos import motion_metrics_pb2

import plotly.graph_objs as go
from plotly.subplots import make_subplots

In [6]:
from waymo_open_dataset.protos import scenario_pb2 

# 데이터셋 로드
dataset = tf.data.TFRecordDataset(filename, compression_type='')
for data in dataset :
   scenario = scenario_pb2.Scenario()
   scenario.ParseFromString(data.numpy())
   break

In [8]:
scenario.scenario_id

'19a486cd29abd7a7'

## MapFeature

In [245]:
for i, s in enumerate(scenario.map_features) :
  if s.HasField('driveway') :
    print(i)
    break

132


### plotly layout 설정

In [222]:
def fig_update_layout(fig, title) :
  fig.update_layout(
      width=1000,
      height=500,
      margin=dict(
          t=50, b=20, l=20, r=20
      ),
      grid=None,
      title={
          'text' : title, #f"Scenario ID : {scenario.scenario_id}",
          'y': 0.95,
          'x': 0.5,
          'xanchor': 'center',
          'yanchor': 'top'
      },
      xaxis1={
        'showticklabels': False,
        'showgrid': False
      },
      yaxis1={
          'showticklabels': False,
          'showgrid': False
      },
      xaxis2={
        'showticklabels': False,
        'showgrid': False
      },
      yaxis2={
          'showticklabels': False,
          'showgrid': False
      },
      
      #plot_bgcolor='gray'
      #template='plotly_dark'
  )

### MapFeature의 Field 체크

In [270]:
def check_feature(fig, feature, row, col) :
  '''
  MapFeature의 필드를 확인하여 해당 필드를 그려주는 함수 호출

  Args :
    scenario.map_features 중 하나
  '''

  if feature.HasField('lane'):
    draw_lanecenter(fig, feature, row, col)

  elif feature.HasField('road_line'):
    draw_roadline(fig, feature, row, col)

  elif feature.HasField('road_edge'):
    draw_roadedge(fig, feature, row, col)

  elif feature.HasField('stop_sign'):
    draw_stopsign(fig, feature, row, col)
  
  elif feature.HasField('crosswalk'):
    draw_crosswalk(fig, feature, row, col)
  
  elif feature.HasField('speed_bump'):
    draw_speedbump(fig, feature, row, col)
  
  elif feature.HasField('driveway'):
    draw_driveway(fig, feature, row, col)
  
  else:
    print("No feature data found.")


### 시작 함수

In [224]:
def start_draw(feature_name) :
  fig = make_subplots(rows=1, cols=2, horizontal_spacing=0.05)

  for s in scenario.map_features :
    if s.HasField(feature_name) :
      check_feature(fig, s, row=1, col=1)
    check_feature(fig, s, row=1, col=2)

  fig_update_layout(fig, feature_name) 
  fig.show()

### LaneCenter

In [196]:
import plotly.graph_objs as go

def draw_lanecenter(fig, feature, row, col) :
  x = []
  y = []
  
  for position in feature.lane.polyline :
    x.append(position.x)
    y.append(position.y)

  fig.add_trace(
      go.Scatter(x=x, y=y, mode='markers', 
        marker=dict(
          color='gray',   # 색상을 회색으로 지정
          size=4,         # 마커 크기
          line=dict(
            color='gray',   # 마커 테두리 색상을 회색으로 지정
            width=1         # 마커 테두리 두께
          )), showlegend=False
      ), row=row, col=col)

start_draw('lane')

### RoadLine

In [203]:
def draw_roadline(fig, feature, row, col) :
  x = []
  y = []

  for position in feature.road_line.polyline :
    x.append(position.x)
    y.append(position.y)
  
  fig.add_trace(
      go.Scatter(x=x, y=y, mode='lines', 
        line=dict(
          color='black', 
          width=1    
        ), showlegend=False
      ), row=row, col=col)

start_draw('road_line')

### RoadEdge

In [225]:
def draw_roadedge(fig, feature, row, col) :
  x = []
  y = []

  for position in feature.road_edge.polyline :
    x.append(position.x)
    y.append(position.y)
  
  fig.add_trace(
      go.Scatter(x=x, y=y, mode='lines', 
        line=dict(
          color='black', 
          width=1    
        ), showlegend=False
      ), row=row, col=col)
  
start_draw('road_edge')

### StopSign

In [233]:
def draw_stopsign(fig, feature, row, col) :
  x = [feature.stop_sign.position.x]
  y = [feature.stop_sign.position.y]
  
  fig.add_trace(
      go.Scatter(x=x, y=y, mode='markers', 
        marker=dict(
          color='red', 
          size=8,    
        ), line_width=1, showlegend=False
      ), row=row, col=col)
  
start_draw('stop_sign')


### Crosswalk

In [240]:
def draw_crosswalk(fig, feature, row, col) :
  x = []
  y = []

  for position in feature.crosswalk.polygon :
    x.append(position.x)
    y.append(position.y)

  # 아래 테두리가 그려지지 않아서 추가함
  x.append(x[0])
  y.append(y[0])
  
  fig.add_trace(
      go.Scatter(x=x, y=y, mode='lines', fill='toself', fillcolor='white',
        line=dict(
          color='black',
          width=1    
        ), showlegend=False
      ), row=row, col=col)

  
start_draw('crosswalk')

### SpeedBump

In [244]:
def draw_speedbump(fig, feature, row, col) :
  x = []
  y = []

  for position in feature.speed_bump.polygon :
    x.append(position.x)
    y.append(position.y)

  # 아래 테두리가 그려지지 않아서 추가함
  x.append(x[0])
  y.append(y[0])
  
  fig.add_trace(
      go.Scatter(x=x, y=y, mode='lines', fill='toself', fillcolor='white',
        line=dict(
          color='yellow',
          width=2    
        ), showlegend=False
      ), row=row, col=col)
  
start_draw('speed_bump')

### Driveway

In [251]:
def draw_driveway(fig, feature, row, col) :
  x = []
  y = []

  for position in feature.driveway.polygon :
    x.append(position.x)
    y.append(position.y)

  # 아래 테두리가 그려지지 않아서 추가함
  x.append(x[0])
  y.append(y[0])
  
  fig.add_trace(
      go.Scatter(x=x, y=y, mode='lines', fill='toself', fillcolor='beige',
        line=dict(
          color='black',
          width=1   
        ), showlegend=False
      ), row=row, col=col)

  
start_draw('driveway')

### MapFeature 최종

In [257]:
fig = make_subplots(rows=1, cols=1)

for s in scenario.map_features :
  check_feature(fig, s, row=1, col=1)

fig_update_layout(fig, 'MapFeature') 
fig.update_layout(
    width=800,
    height=800,
)
fig.show()

## DynamicMapState

### TrafficSignalLaneState

In [300]:
def draw_lanestates(fig, lane_states, row=1, col=1) :

  x = []
  y = []

  for lane in lane_states :
    x.append(lane.stop_point.x)
    y.append(lane.stop_point.y)
  

  fig.add_trace(
      go.Scatter(x=x, y=y, mode='markers', 
        marker=dict(
          color='green',
          size=10   
        ), line_width=1, showlegend=False
      ), row=row, col=col)


fig = make_subplots(rows=1, cols=2)


for s in scenario.map_features :
  check_feature(fig, s, row=1, col=1)

for l in scenario.dynamic_map_states :
  draw_lanestates(fig, l.lane_states, row=1, col=1)
  draw_lanestates(fig, l.lane_states, row=1, col=2)
  break

fig_update_layout(fig, 'TrafficSignalLaneState') 
fig.show()


## Tracks (Agent)

In [299]:
scenario.tracks[0].states[0]

center_x: 8382.083984375
center_y: 7213.89013671875
center_z: -13.732300758361816
length: 4.414564609527588
width: 1.943734884262085
height: 1.4712934494018555
heading: -1.5578702688217163
velocity_x: 0.146484375
velocity_y: -19.8193359375
valid: true

In [303]:
def draw_agent(fig, object_states, row=1, col=1) :

  x = []
  y = []

  for agent in object_states :
    if agent.valid :
      x.append(agent.center_x)
      y.append(agent.center_y)
    break
  
  
  fig.add_trace(
      go.Scatter(x=x, y=y, mode='markers', 
        marker=dict(
          color='blue',
          size=10,
          symbol='square' 
        ), line_width=1, showlegend=False
      ), row=row, col=col)


fig = make_subplots(rows=1, cols=2)


for s in scenario.map_features :
  check_feature(fig, s, row=1, col=2)

for l in scenario.dynamic_map_states :
  draw_lanestates(fig, l.lane_states, row=1, col=2)
  break

for t in scenario.tracks :
  draw_agent(fig, t.states, row=1, col=1)
  draw_agent(fig, t.states, row=1, col=2)

fig_update_layout(fig, 'TrafficSignalLaneState') 
fig.show()


## 정적 시각화 최종

In [307]:
fig = make_subplots(rows=1, cols=1)


for s in scenario.map_features :
  check_feature(fig, s, row=1, col=1)

for l in scenario.dynamic_map_states :
  draw_lanestates(fig, l.lane_states, row=1, col=1)
  break

for t in scenario.tracks :
  draw_agent(fig, t.states, row=1, col=1)

fig_update_layout(fig, 'Final') 
fig.update_layout(width=800, height=800) 
fig.show()